In [23]:
import pandas as pd
import folium
import folium.plugins as plugins
from IPython.display import display
from datetime import datetime, timedelta

## Read data from excel spreadsheet

In [2]:
data_path = "./raw_data/export_dashboard_x_uk_x_filter_nativeretweets_geocode_55_378051_3_43597299999999_750km_2016_04_21_10_32_03.xlsx"
df_stream = pd.read_excel(data_path, sheet_name="Stream")

In [3]:
display(df_stream)

Tweet Id        Date   Hour        User Name  \
0       723066388391157762  2016-04-21  08:30              ZPR   
1       723066384297672704  2016-04-21  08:30       Beep!Beep!   
2       723066381751689216  2016-04-21  08:30          Annette   
3       723066348201353216  2016-04-21  08:30     Dollie Henry   
4       723066340953722880  2016-04-21  08:30   Cleo Bannister   
...                    ...         ...    ...              ...   
169028  720548358369185792  2016-04-14  09:44      Dawn Carter   
169029  720548357706530816  2016-04-14  09:44    Hywel Roberts   
169030  720548341738795008  2016-04-14  09:44        Alex Hall   
169031  720548323774611456  2016-04-14  09:44            beLLa   
169032  720548256497930240  2016-04-14  09:44  Gabriella McCoy   

               Nickname                                                Bio  \
0               ZPRSoho  22 straight talking PRs based in Soho sharing ...   
1       BeepBeepTraffic  UK Traffic Alert App for iOS http://t.co/55H1q...   
2       annetteand2dogs  Sociologist, (vintage) cyclist, dog lover, mus...   
3           DollieHenry  Choreographer | Theatre Director | Educator | ...   
4        cleo_bannister  Love reading and reviewing.  Struggle with an ...   
...                 ...                                                ...   
169028       DawnieBate                                                NaN   
169029    HywelRoberts2  Deputy editor at Works Management and contribu...   
169030           devseo  Looking for an SEO and Development Engineer th...   
169031     nabilariduan  Kau pernah sayang seseorang more than everythi...   
169032   GabriellaMcCoy                     Say it loud and go from there.   

                                            Tweet content  Favs  RTs  \
0       Talking to some great journos this morning all...   NaN  NaN   
1       Incident (Severe delay) M6 northbound between ...   NaN  NaN   
2       THIS: “@Colmogorman: Great piece by @amcteirna...   NaN  NaN   
3       A Little snippet from my #SundayJazzCongregati...   NaN  NaN   
4       Latest Book Review: The Closet of Savage Memen...   NaN  NaN   
...                                                   ...   ...  ...   
169028  #beautiful #green #somerset #levels #love #liv...   NaN  NaN   
169029                          @stephenkb Well indeed...   NaN  NaN   
169030  https://t.co/Rwju1X0nAC - How to Communicate E...   NaN  NaN   
169031  Dah sampaiiii (@ Manchester International Airp...   1.0  NaN   
169032  Vegas - we comin' #preparethepoolparty #sincit...   NaN  NaN   

         Latitude  Longitude Country          Place (as appears on Bio)  \
0       51.505185  -0.150128      GB                    London, England   
1       52.615627  -2.029030      GB                Willenhall, England   
2       53.336995  -6.279686      IE               Dublin City, Ireland   
3       51.513451  -0.125331      GB                    London, England   
4       49.201770  -2.114542      GB  Saint Helier, Bailiwick of Jersey   
...           ...        ...     ...                                ...   
169028  51.118702  -2.915014      GB                South West, England   
169029  51.424421   0.232808      GB                 Hawley, South East   
169030  54.063300  -2.884240      GB                 Middleton, England   
169031  53.362359  -2.274299      GB                Manchester, England   
169032  51.157837  -0.169274      GB                South East, England   

                                          Profile picture  Followers  \
0       http://pbs.twimg.com/profile_images/3788000006...     2178.0   
1       http://pbs.twimg.com/profile_images/4657702836...      458.0   
2       http://pbs.twimg.com/profile_images/6648605106...      333.0   
3       http://pbs.twimg.com/profile_images/7205554601...     1259.0   
4       http://pbs.twimg.com/profile_images/3788000006...     2418.0   
...                                                   ...        ...   
169028  http://pbs

## HeatMap of all twits

In [4]:
df_to_map = pd.DataFrame({"datetime": pd.to_datetime(df_stream.Date + "-" + df_stream.Hour, format="%Y-%m-%d-%H:%M"),
                         "nickname": df_stream.Nickname,
                          #"location": zip(df.Latitude, df.Longitude)
                         "latitude": df_stream.Latitude, 
                         "longitude": df_stream.Longitude
                         })
df_to_map = df_to_map.set_index('datetime')
df_to_map = df_to_map.sort_index()
df_to_map = df_to_map.dropna()
df_to_map["location"] = list(zip(df_to_map.latitude, df_to_map.longitude))

In [5]:
print(len(df_to_map))

169020


In [6]:
m = folium.Map([48., 5.],
               tiles='stamentoner',
               zoom_start=6)

# hm = plugins.HeatMapWithTime(
#     data=df_to_map["location"].to_list(),
#     index=df_to_map.index.to_list(),
#     auto_play=True,
#     max_opacity=0.3,
# )

hm = plugins.HeatMap(
    data=df_to_map["location"].to_list(),
    max_opacity=0.3
)

hm.add_to(m)

In [7]:
m

## Filtering tweets by most popular hashtags

In [67]:
TOP_NUM = 10
top_hash_data_path = "./raw_data/export_content_x_uk_x_filter_nativeretweets_geocode_55_378051_3_43597299999999_750km_2016_04_21_11_46_43.xlsx"
df_top_hashtags = pd.read_excel(top_hash_data_path, sheet_name="Top Hashtags", nrows=TOP_NUM)

In [68]:
display(df_top_hashtags)

Hash  Repeats
0  nowplaying     5300
1      Hiring     2920
2    areacode     2407
3         tnc     2407
4         job     2157
5         Job     2154
6      london     2068
7   CareerArc     2039
8        Jobs     1933
9      London     1831

In [69]:
dfs_hash = dict()
for i in range(TOP_NUM):
    hashtag = str(df_top_hashtags["Hash"][i])
    df_hash = pd.DataFrame({"datetime": pd.to_datetime(df_stream.Date + "-" + df_stream.Hour, format="%Y-%m-%d-%H:%M"),
                         "nickname": df_stream.Nickname,
                          #"location": zip(df.Latitude, df.Longitude)
                         "latitude": df_stream.Latitude, 
                         "longitude": df_stream.Longitude
                         })[df_stream["Tweet content"].str.contains("#" + hashtag)]
    df_hash = df_hash.set_index("datetime")
    df_hash = df_hash.sort_index()
    df_hash = df_hash.dropna()
    df_hash["location"] = list(zip(df_hash.latitude, df_hash.longitude))
    print("{}: {}".format(hashtag, len(df_hash)))
    dfs_hash[hashtag] = df_hash

nowplaying: 5300
Hiring: 2920
areacode: 2407
tnc: 2407
job: 2177
Job: 2156
london: 2491
CareerArc: 2039
Jobs: 1933
London: 2024


In [75]:
m_hashes = folium.Map([48., 5.],
               tiles='stamentoner',
               zoom_start=6)

# for i in range(TOP_NUM):
#     hashtag = str(df_top_hashtags["Hash"][i])
#     df_hash = dfs_hash[hashtag]
#     hm_hash = plugins.HeatMap(
#         data=df_hash["location"].to_list(),
#         max_opacity=0.3
#     )
#     hm_hash.add_to(m_hashes)

hashtag = str(df_top_hashtags["Hash"][1])
df_hash = dfs_hash[hashtag]
hm_hash = plugins.HeatMap(
    data=df_hash["location"].to_list(),
    max_opacity=0.3
)
hm_hash.add_to(m_hashes)

In [76]:
print(hashtag)
m_hashes

Hiring


## Hashtag heatmap with time

In [77]:
m_time = folium.Map([48., 5.],
               tiles='stamentoner',
               zoom_start=6)

time_index = df_hash.index.strftime('%Y-%m-%d').unique().to_list()
points_over_time = [df_hash[df_hash.index.strftime('%Y-%m-%d')==t]["location"].to_list() for t in time_index ]

weight = 1  # default value
for time_entry in points_over_time:
    for i in range(len(time_entry)):
        time_entry[i] = list(time_entry[i])
        time_entry[i].append(weight)

hm_time = plugins.HeatMapWithTime(
    data=points_over_time,
    index=time_index,
    auto_play=True,
    max_opacity=0.3,
)

hm_time.add_to(m_time)

In [78]:
print(hashtag)
m_time

Hiring
